# Cow + Univ3 DataPipeline

### Setup Jupyter Environment

In [57]:
from datastreams.datastream import Streamer

# import concurrent.futures
import os
import pandas as pd
import polars as pl

# These commands enlarge the column size of the dataframe so things like 0x... are not truncated
pd.set_option('display.max_columns', None)
pd.set_option('display.expand_frame_repr', False)
pd.set_option('max_colwidth', None)

### Cowswap Trades

In [58]:
# instantiate Streamer class. Note that we need two separate streamer classes, otherwise the queries will be overwritten. 
cow_ds1 = Streamer('https://api.thegraph.com/subgraphs/name/cowprotocol/cow')
cow_ds2 = Streamer('https://api.thegraph.com/subgraphs/name/cowprotocol/cow')

In [59]:
# DEFINE TIMESTAMP HERE. Timstamp is used for replication quality assurance purposes.
timestamp = 1677891498 # current block timestamp is around 1677891498 on March 3rd, 2023 8:06PM

# define ethereum token addresses here to be used in cowswap trades query filter
weth_addr = "0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2"
usdc_addr = "0xa0b86991c6218b36c1d19d4a2e9eb0ce3606eb48"

# we set a fixed query size number. The Cow settlements and Uniswap swaps query are multiples larger than this initial query size.
query_size = 10000000

#Filter size - We filter trades out that are smaller than $1000 USD size
filter_usd = 1000

In [60]:
token_addr_list = [weth_addr, usdc_addr]

In [61]:
# We need to make two queries to the cow schema to get all the trades that match weth/usdc and usdc/weth.
trades_weth_usdc_fp = cow_ds1.queryDict.get('trades')
trades_usdc_weth_fp = cow_ds2.queryDict.get('trades')

# trades query path that gets token a -> token b trades
trades_weth_usdc_qp = trades_weth_usdc_fp(
    first=query_size,
    orderBy='timestamp',
    orderDirection='desc',
    where = {
    'timestamp_lt': timestamp, 
    'buyAmountUsd_gt': filter_usd, 
    'sellAmountUsd_gt': filter_usd, 
    "sellToken_in": token_addr_list, 
    "buyToken_in": token_addr_list
    }
)

# trades query path that gets token b -> token a trades
trades_usdc_weth_qp = trades_usdc_weth_fp(
    first=query_size,
    orderBy='timestamp',
    orderDirection='desc',
    where = {
    'timestamp_lt': timestamp, 
    'buyAmountUsd_gt': filter_usd, 
    'sellAmountUsd_gt': filter_usd, 
    "sellToken_in": token_addr_list, 
    "buyToken_in": token_addr_list
    }
)

# run query
trades_weth_usdc_df = cow_ds1.runQuery(trades_weth_usdc_qp)
trades_usdc_weth_df = cow_ds2.runQuery(trades_usdc_weth_qp)

FIELD - trades
FIELD - trades


In [62]:
# combine the trades queries together
trades_df = pd.concat([trades_weth_usdc_df, trades_usdc_weth_df])

In [63]:
print(f'query returned {len(trades_df)} rows')

query returned 43696 rows


In [64]:
# verify the query results to ensure that only two tokens were queried.
trades_df['trades_buyToken_id'].unique()

array(['0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2',
       '0xa0b86991c6218b36c1d19d4a2e9eb0ce3606eb48'], dtype=object)

In [65]:
# replace addresses with symbols
trades_df['trades_buyToken_id'] = trades_df['trades_buyToken_id'].replace(weth_addr, 'WETH')
trades_df['trades_buyToken_id'] = trades_df['trades_buyToken_id'].replace(usdc_addr, 'USDC')

trades_df['trades_sellToken_id'] = trades_df['trades_sellToken_id'].replace(weth_addr, 'WETH')
trades_df['trades_sellToken_id'] = trades_df['trades_sellToken_id'].replace(usdc_addr, 'USDC')

In [66]:
trades_df.columns

Index(['trades_id', 'trades_timestamp', 'trades_gasPrice', 'trades_feeAmount',
       'trades_txHash', 'trades_settlement_id', 'trades_buyAmount',
       'trades_sellAmount', 'trades_sellToken_id', 'trades_buyToken_id',
       'trades_order_id', 'trades_buyAmountEth', 'trades_sellAmountEth',
       'trades_buyAmountUsd', 'trades_sellAmountUsd', 'endpoint'],
      dtype='object')

### Cowswap Trades-Settlement Merge

In [67]:
# do same query methood but instead of timestamps, use trades_settlement_id

# get unique trades_settlement_id list
trades_settlement_id_list = trades_df['trades_settlement_id'].unique()

# define field path
settlements_fp = cow_ds1.queryDict.get('settlements')

In [68]:
settlement_df_list = []

In [69]:
for i in range(0, len(trades_settlement_id_list)): # inner loop through cowswap timestamps
    print(f'round {i} of {len(trades_settlement_id_list)}')
    # define the query path
    settlements_qp = settlements_fp(
        first=query_size * 3,
        orderBy='firstTradeTimestamp',
        orderDirection='desc',
        where = {'txHash': trades_settlement_id_list[i]} 
        )
    
    # run query
    df = cow_ds1.runQuery(settlements_qp)

    if df.empty:
        print('empty')
        continue
    else:
        settlement_df_list.append(df)

round 0 of 20628
FIELD - settlements
round 1 of 20628
FIELD - settlements
round 2 of 20628
FIELD - settlements
round 3 of 20628
FIELD - settlements
round 4 of 20628
FIELD - settlements
round 5 of 20628
FIELD - settlements
round 6 of 20628
FIELD - settlements
round 7 of 20628
FIELD - settlements
round 8 of 20628
FIELD - settlements
round 9 of 20628
FIELD - settlements
round 10 of 20628
FIELD - settlements
round 11 of 20628
FIELD - settlements
round 12 of 20628
FIELD - settlements
round 13 of 20628
FIELD - settlements
round 14 of 20628
FIELD - settlements
round 15 of 20628
FIELD - settlements
round 16 of 20628
FIELD - settlements
round 17 of 20628
FIELD - settlements
round 18 of 20628
FIELD - settlements
round 19 of 20628
FIELD - settlements
round 20 of 20628
FIELD - settlements
round 21 of 20628
FIELD - settlements
round 22 of 20628
FIELD - settlements
round 23 of 20628
FIELD - settlements
round 24 of 20628
FIELD - settlements
round 25 of 20628
FIELD - settlements
round 26 of 20628
FIEL

In [70]:
# concatenate
settlements_df = pd.concat(settlement_df_list)

In [71]:
# enforce trades_df column types. This is necessary because the data types are not enforced by pandas dataframes. We need to enforce the types as a preprocessing step to converting to Polars
trades_df['trades_buyAmount'] = trades_df['trades_buyAmount'].astype('float64')
trades_df['trades_sellAmount'] = trades_df['trades_sellAmount'].astype('float64')
trades_df['trades_buyAmountUsd'] = trades_df['trades_buyAmountUsd'].astype('float64')
trades_df['trades_sellAmountUsd'] = trades_df['trades_sellAmountUsd'].astype('float64')
trades_df['trades_timestamp'] = trades_df['trades_timestamp'].astype('int64')
trades_df['trades_buyToken_id'] = trades_df['trades_buyToken_id'].astype('str')
trades_df['trades_sellToken_id'] = trades_df['trades_sellToken_id'].astype('str')

In [72]:
# convert dictionaries into polars dataframes
settlement_pl = pl.from_pandas(settlements_df)
trades_pl = pl.from_pandas(trades_df)

In [73]:
# merge trades and settlement dataframes on the settlement transaction hash
cow_trades_pl = trades_pl.join(other=settlement_pl, left_on='trades_settlement_id', right_on='settlements_txHash', how='inner')

In [74]:
cow_trades_pl.shape

(43696, 20)

In [75]:
cow_trades_pl.head(5)

shape: (5, 20)
┌─────────┬────────────┬────────────┬────────────┬─────┬────────────┬────────────┬────────────┬────────────┐
│ trades_ ┆ trades_tim ┆ trades_gas ┆ trades_fee ┆ ... ┆ settlement ┆ settlement ┆ settlement ┆ endpoint_r │
│ id      ┆ estamp     ┆ Price      ┆ Amount     ┆     ┆ s_id       ┆ s_firstTra ┆ s_solver_i ┆ ight       │
│ ---     ┆ ---        ┆ ---        ┆ ---        ┆     ┆ ---        ┆ deTimestam ┆ d          ┆ ---        │
│ str     ┆ i64        ┆ i64        ┆ i64        ┆     ┆ str        ┆ p          ┆ ---        ┆ str        │
│         ┆            ┆            ┆            ┆     ┆            ┆ ---        ┆ str        ┆            │
│         ┆            ┆            ┆            ┆     ┆            ┆ i64        ┆            ┆            │
╞═════════╪════════════╪════════════╪════════════╪═════╪════════════╪════════════╪════════════╪════════════╡
│ 0x2d177 ┆ 1677890687 ┆ 3403193858 ┆ 11504283   ┆ ... ┆ 0xdbeb3db4 ┆ 1677890687 ┆ 0x149d0f92 ┆ cow        │
│ cbcc3e2 ┆            ┆ 1          ┆            ┆     ┆ bf019dac72 ┆            ┆ 82333681ee ┆            │
│ 66aa322 ┆            ┆            ┆            ┆     ┆ 1970e0eed1 ┆            ┆ 41d3058982 ┆            │
│ fff7f41 ┆            ┆            ┆            ┆     ┆ 75...      ┆            ┆ 4b...      ┆            │
│ 2305... ┆            ┆            ┆            ┆     ┆            ┆            ┆            ┆            │
│ 0x47ece ┆ 1677887663 ┆ 3009611088 ┆ 39337855   ┆ ... ┆ 0x8810dcd2 ┆ 1677887663 ┆ 0x149d0f92 ┆ cow        │
│ 80491bf ┆            ┆ 4          ┆            ┆     ┆ 471391d3c6 ┆            ┆ 82333681ee ┆            │
│ 75fd702 ┆            ┆            ┆            ┆     ┆ cc430a8080 ┆            ┆ 41d3058982 ┆            │
│ 5549f9e ┆            ┆            ┆            ┆     ┆ a1...      ┆            ┆ 4b...      ┆            │
│ 88c7... ┆            ┆            ┆            ┆     ┆            ┆            ┆            ┆            │
│ 0x8c129 ┆ 1677885323 ┆ 1968935519 ┆ 27018672   ┆ ... ┆ 0xf8e2a0e1 ┆ 1677885323 ┆ 0xb20b86c4 ┆ cow        │
│ 381cf3e ┆            ┆ 8          ┆            ┆     ┆ ae139b4b4a ┆            ┆ e6deeb432a ┆            │
│ a5e26a1 ┆            ┆            ┆            ┆     ┆ f587b97058 ┆            ┆ 22d773a221 ┆            │
│ ccdec20 ┆            ┆            ┆            ┆     ┆ 95...      ┆            ┆ 89...      ┆            │
│ b070... ┆            ┆            ┆            ┆     ┆            ┆            ┆            ┆            │
│ 0xc07f4 ┆ 1677882191 ┆ 2122076543 ┆ 4843587156 ┆ ... ┆ 0x4eadf538 ┆ 1677882191 ┆ 0xc9ec550b ┆ cow        │
│ 5a19d95 ┆            ┆ 2          ┆ 540876     ┆     ┆ 41770fb1ba ┆            ┆ ea1c64d779 ┆            │
│ d27214a ┆            ┆            ┆            ┆     ┆ 903817d7e3 ┆            ┆ 124b23a262 ┆            │
│ 7be024c ┆            ┆            ┆            ┆     ┆ 7d...      ┆            ┆ 92...      ┆            │
│ f2e4... ┆            ┆            ┆            ┆     ┆            ┆            ┆            ┆            │
│ 0x7159b ┆ 1677882011 ┆ 2151573490 ┆ 3250564090 ┆ ... ┆ 0xfb4569f8 ┆ 1677882011 ┆ 0x149d0f92 ┆ cow        │
│ 0217959 ┆            ┆ 6          ┆ 489318     ┆     ┆ 5710f1ba09 ┆            ┆ 82333681ee ┆            │
│ de58857 ┆            ┆            ┆            ┆     ┆ 3f1001277b ┆            ┆ 41d3058982 ┆            │
│ 8921983 ┆            ┆            ┆            ┆     ┆ db...      ┆            ┆ 4b...      ┆            │
│ bd06... ┆            ┆            ┆            ┆     ┆            ┆            ┆            ┆            │
└─────────┴────────────┴────────────┴────────────┴─────┴────────────┴────────────┴────────────┴────────────┘

In [76]:
# get unique values in cow_trades_pl trades_sellToken_id column
cow_trades_pl['trades_sellToken_id'].unique()

shape: (2,)
Series: 'trades_sellToken_id' [str]
[
	"USDC"
	"WETH"
]

### Cowswap Trades-Solver Merge

In [77]:
solvers = pd.read_csv('data/cowv2_solvers.csv') # load in pandas instead of polars. Having trouble replacing \ symbol in polars

In [78]:
# rename address to settlements_solver_id in pandas
solvers = solvers.rename(columns={"address": "settlements_solver_id"})

In [79]:
# NOTE - dune formats addresses as /x... need to convert '/' to '0'
solvers['settlements_solver_id'] = solvers['settlements_solver_id'].str.replace('\\', '0', regex=False)

In [80]:
# turn solvers into a dictionary
solvers_dict = solvers.to_dict('records')

# convert dict to polars
solvers_pl = pl.from_dicts(solvers_dict)

In [81]:
# inner join solvers_pl on total_settlement_tokens_pl
cow_complete_pl = cow_trades_pl.join(solvers_pl, on="settlements_solver_id", how="inner")

In [82]:
# drop endpoint_right column from total_settlement_tokens_solvers
cow_complete_pl = cow_complete_pl.drop('endpoint_right')

In [83]:
cow_complete_pl.shape

(43514, 22)

In [84]:
# save polars to parquet
cow_complete_pl.write_parquet('data/cow_complete_pl.parquet')

#### Basic Agg

In [85]:
# filter by "prod" environments
filter_df = cow_complete_pl.filter(pl.col("environment") == "prod")

In [86]:
# filter by "prod" environments
filter_df = cow_complete_pl.filter(pl.col("environment") == "prod")

In [87]:
filter_df.shape

(42310, 22)

In [88]:
# group filter_df by solver name. Check solver count
grouped_df = filter_df.groupby("name").agg(
    pl.count("trades_id").alias("total_trades")).sort("total_trades", reverse=True)


In [89]:
grouped_df

shape: (16, 2)
┌────────────────────┬──────────────┐
│ name               ┆ total_trades │
│ ---                ┆ ---          │
│ str                ┆ u32          │
╞════════════════════╪══════════════╡
│ Otex               ┆ 6510         │
│ PLM                ┆ 6020         │
│ Gnosis_0x          ┆ 5866         │
│ Gnosis_1inch       ┆ 4568         │
│ ...                ┆ ...          │
│ Quasilabs          ┆ 956          │
│ Atlas              ┆ 210          │
│ Gnosis_BalancerSOR ┆ 200          │
│ Seasolver          ┆ 164          │
└────────────────────┴──────────────┘

### Uniswap V3 Swaps

In [90]:
# instantiate Streamer object. 
# Note - unlike the cow queries, univ3 does not require multiple streamer instantations because the swaps field path is reset each iteration. 
# If the Cow queries were updated to use the same method, we could use the same streamer object for all queries.
univ3_ds = Streamer('https://api.thegraph.com/subgraphs/name/messari/uniswap-v3-ethereum')

In [91]:
# get a query field path from the query dictionary which is automatically populated in the Streamer object
swaps_fp = univ3_ds.queryDict.get('swaps')

In [92]:
weth_usdc_list = [
    "0x88e6a0c2ddd26feeb64f039a2c41296fcb3f5640", # usdc/weth .05%
    "0x8ad599c3a0ff1de082011efddc58f1908eb6e6d8" #usdc/weth .3%
]

In [93]:
timestamps_list = cow_complete_pl['trades_timestamp'].to_list()
# get unique values in cow_timestamps
cow_timestamps = list(set(timestamps_list))

swaps_df_list = []

In [94]:
for lp in weth_usdc_list: # outer loop loops through liquidity pools
    for i in range(0, len(cow_timestamps)): # inner loop through cowswap timestamps
        print(f'round {i} of {len(cow_timestamps)}, timestamp: {cow_timestamps[i]}')
        # define the query path
        swaps_qp = swaps_fp(
            first=10,
            orderBy='timestamp',
            orderDirection='desc',
            where = {'timestamp_lt': cow_timestamps[i], 'amountInUSD_gt': filter_usd, 'amountOutUSD_gt': filter_usd, 'pool': lp} 
            )

        # run query
        df = univ3_ds.runQuery(swaps_qp)

        if df.empty:
            print('empty')
            continue
        else:
            swaps_df_list.append(df)

round 0 of 20512, timestamp: 1648623621
FIELD - swaps
round 1 of 20512, timestamp: 1652555791
FIELD - swaps
round 2 of 20512, timestamp: 1634992143
FIELD - swaps
round 3 of 20512, timestamp: 1674575891
FIELD - swaps
round 4 of 20512, timestamp: 1664221211
FIELD - swaps
round 5 of 20512, timestamp: 1636565026
FIELD - swaps
round 6 of 20512, timestamp: 1633681442
FIELD - swaps
round 7 of 20512, timestamp: 1673658407
FIELD - swaps
round 8 of 20512, timestamp: 1661468720
FIELD - swaps
round 9 of 20512, timestamp: 1638006837
FIELD - swaps
round 10 of 20512, timestamp: 1636696118
FIELD - swaps
round 11 of 20512, timestamp: 1636565047
FIELD - swaps
round 12 of 20512, timestamp: 1636433974
FIELD - swaps
round 13 of 20512, timestamp: 1640366138
FIELD - swaps
round 14 of 20512, timestamp: 1661993031
FIELD - swaps
round 15 of 20512, timestamp: 1669988435
FIELD - swaps
round 16 of 20512, timestamp: 1639317593
FIELD - swaps
round 17 of 20512, timestamp: 1669070951
FIELD - swaps
round 18 of 20512, t

In [95]:
# concat swaps_df_list into a single dataframe.
swaps_df = pd.concat(swaps_df_list)

In [96]:
swaps_df.shape

(410240, 20)

In [97]:
# print min and max swaps_timestamp
print(swaps_df['swaps_timestamp'].min())
print(swaps_df['swaps_timestamp'].max())

1628255444
1677890675


In [98]:
# replace the pool addresses with LP pool names with fees
swaps_df['swaps_pool_id'] = swaps_df['swaps_pool_id'].replace(weth_usdc_list[0], 'USDC_WETH .05%')
swaps_df['swaps_pool_id'] = swaps_df['swaps_pool_id'].replace(weth_usdc_list[1], 'USDC_WETH .3%')

# replace token addresses with symbols
swaps_df['swaps_tokenIn_id'] = swaps_df['swaps_tokenIn_id'].replace(usdc_addr, 'USDC')
swaps_df['swaps_tokenIn_id'] = swaps_df['swaps_tokenIn_id'].replace(weth_addr, 'WETH')
swaps_df['swaps_tokenOut_id'] = swaps_df['swaps_tokenOut_id'].replace(usdc_addr, 'USDC')
swaps_df['swaps_tokenOut_id'] = swaps_df['swaps_tokenOut_id'].replace(weth_addr, 'WETH')

In [99]:
print(f'query returned {len(swaps_df)} rows\n swaps_df columns are {swaps_df.columns}')

query returned 410240 rows
 swaps_df columns are Index(['swaps_id', 'swaps_hash', 'swaps_nonce', 'swaps_logIndex',
       'swaps_gasLimit', 'swaps_gasUsed', 'swaps_gasPrice',
       'swaps_protocol_id', 'swaps_account_id', 'swaps_pool_id',
       'swaps_blockNumber', 'swaps_timestamp', 'swaps_tick',
       'swaps_tokenIn_id', 'swaps_amountIn', 'swaps_amountInUSD',
       'swaps_tokenOut_id', 'swaps_amountOut', 'swaps_amountOutUSD',
       'endpoint'],
      dtype='object')


In [100]:
# NOTES swaps_gasLimit, swaps_gasPrice are the two columns to calculate gas

In [101]:
# save polars to parquet
swaps_df.to_csv('data/swaps_df.csv')

In [102]:
# enforce swaps_df column types. This is necessary because the data types are not enforced by pandas dataframes. We need to enforce the types as a preprocessing step to converting to Polars
swaps_df['swaps_gasLimit'] = swaps_df['swaps_gasLimit'].astype('float64')
swaps_df['swaps_gasUsed'] = swaps_df['swaps_gasUsed'].astype('float64')
swaps_df['swaps_gasPrice'] = swaps_df['swaps_gasPrice'].astype('float64')
swaps_df['swaps_amountIn'] = swaps_df['swaps_amountIn'].astype('float64')
swaps_df['swaps_amountInUSD'] = swaps_df['swaps_amountInUSD'].astype('float64')
swaps_df['swaps_amountOut'] = swaps_df['swaps_amountOut'].astype('float64')
swaps_df['swaps_amountOutUSD'] = swaps_df['swaps_amountOutUSD'].astype('float64')
swaps_df['swaps_blockNumber'] = swaps_df['swaps_blockNumber'].astype('int64')
swaps_df['swaps_timestamp'] = swaps_df['swaps_timestamp'].astype('int64')

In [103]:
# load swaps_df.csv
swaps_df = pd.read_csv('data/swaps_df.csv')

In [104]:
# convert swaps, transactions, and cowswap dataframes to polars
swaps_pl = pl.from_pandas(swaps_df)
# recall cow_trades_pl was already created earlier

In [105]:
# drop duplicate rows
uni_complete_pl = swaps_pl.unique()

In [106]:
# drop endpoint column from uni_complete_pl
uni_complete_pl = uni_complete_pl.drop('endpoint')

### Univ3 Gas Calculations

In [107]:
# get median transactions_gasUsed amount. Typical V3 swap is 127k gas for One-hop. However with multiple hops, gas will be higher. 352 reflects an avg of 3 hops worth of gas
tx_gas_median = uni_complete_pl['swaps_gasLimit'].median()
print(f'transaction gas median is {tx_gas_median}')

transaction gas median is 312218.5


In [108]:
# to get transaction gas used, we do gasUsed * gasPrice
uni_complete_pl = uni_complete_pl.with_columns([
    (127000 * pl.col("swaps_gasPrice")).alias('transaction_gas_fee_one_hop'),
    (tx_gas_median * pl.col("swaps_gasPrice")).alias('transaction_gas_fee_median')
    ])

In [109]:
uni_complete_pl = uni_complete_pl.with_columns([
    (pl.col("transaction_gas_fee_one_hop") / 10**18).alias('transaction_gas_fee_one_hop'), # wei is 10^9, but eth is 10^18
        (pl.col("transaction_gas_fee_median") / 10**18).alias('transaction_gas_fee_median') # wei is 10^9, but eth is 10^18
])

In [110]:
# sort by largest transaction_gas_fee
uni_complete_pl.sort("transaction_gas_fee_one_hop", reverse=False).head(5)

shape: (5, 22)
┌──────────┬──────┬──────────┬───────────┬─────┬────────────┬────────────┬────────────┬────────────┐
│ Unnamed: ┆ swap ┆ swaps_ha ┆ swaps_non ┆ ... ┆ swaps_amou ┆ swaps_amou ┆ transactio ┆ transactio │
│ 0        ┆ s_id ┆ sh       ┆ ce        ┆     ┆ ntOut      ┆ ntOutUSD   ┆ n_gas_fee_ ┆ n_gas_fee_ │
│ ---      ┆ ---  ┆ ---      ┆ ---       ┆     ┆ ---        ┆ ---        ┆ one_hop    ┆ median     │
│ i64      ┆ str  ┆ str      ┆ i64       ┆     ┆ str        ┆ f64        ┆ ---        ┆ ---        │
│          ┆      ┆          ┆           ┆     ┆            ┆            ┆ f64        ┆ f64        │
╞══════════╪══════╪══════════╪═══════════╪═════╪════════════╪════════════╪════════════╪════════════╡
│ 1        ┆ 0x8a ┆ 0x8a59e9 ┆ 102188    ┆ ... ┆ 1389633922 ┆ 138963.392 ┆ 0.000218   ┆ 0.000535   │
│          ┆ 59e9 ┆ 9a8b1d0c ┆           ┆     ┆ 81         ┆ 281        ┆            ┆            │
│          ┆ 9a8b ┆ d5c56602 ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 1d0c ┆ db4770d5 ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ d5c5 ┆ ...      ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 6602 ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ db47 ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 70d5 ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ ...  ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│ 4        ┆ 0x8a ┆ 0x8a59e9 ┆ 102188    ┆ ... ┆ 1389633922 ┆ 138963.392 ┆ 0.000218   ┆ 0.000535   │
│          ┆ 59e9 ┆ 9a8b1d0c ┆           ┆     ┆ 81         ┆ 281        ┆            ┆            │
│          ┆ 9a8b ┆ d5c56602 ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 1d0c ┆ db4770d5 ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ d5c5 ┆ ...      ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 6602 ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ db47 ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 70d5 ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ ...  ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│ 9        ┆ 0x8a ┆ 0x8a59e9 ┆ 102188    ┆ ... ┆ 1389633922 ┆ 138963.392 ┆ 0.000218   ┆ 0.000535   │
│          ┆ 59e9 ┆ 9a8b1d0c ┆           ┆     ┆ 81         ┆ 281        ┆            ┆            │
│          ┆ 9a8b ┆ d5c56602 ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 1d0c ┆ db4770d5 ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ d5c5 ┆ ...      ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 6602 ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ db47 ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 70d5 ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ ...  ┆          ┆           ┆     ┆            ┆            ┆            ┆            │
│ 6        ┆ 0x16 ┆ 0x168c1e ┆ 10677     ┆ ... ┆ 3920888143 ┆ 392088.814 ┆ 0.000256   ┆ 0.000629   │
│          ┆ 8c1e ┆ 0450eccb ┆           ┆     ┆ 20         ┆ 32         ┆            ┆            │
│          ┆ 0450 ┆ ac253e4c ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ eccb ┆ e86930b6 ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ ac25 ┆ ...      ┆           ┆     ┆            ┆            ┆            ┆            │
│          ┆ 3e4c ┆          ┆           ┆    

### Merge Cow and Univ3

In [111]:
# load cow_complete_pl.parquet
cow_complete_pl = pl.read_parquet('data/cow_complete_pl.parquet')

In [112]:
# merge trades and swaps on timestamp value. We use outer join because we want to keep all trades and swaps data and backfill swap values
cow_uni_outer_pl = cow_complete_pl.join(other=uni_complete_pl, left_on='trades_timestamp', right_on='swaps_timestamp', how='outer')

In [113]:
cow_uni_outer_pl.columns

['trades_id',
 'trades_timestamp',
 'trades_gasPrice',
 'trades_feeAmount',
 'trades_txHash',
 'trades_settlement_id',
 'trades_buyAmount',
 'trades_sellAmount',
 'trades_sellToken_id',
 'trades_buyToken_id',
 'trades_order_id',
 'trades_buyAmountEth',
 'trades_sellAmountEth',
 'trades_buyAmountUsd',
 'trades_sellAmountUsd',
 'endpoint',
 'settlements_id',
 'settlements_firstTradeTimestamp',
 'settlements_solver_id',
 'environment',
 'name',
 'active',
 'Unnamed: 0',
 'swaps_id',
 'swaps_hash',
 'swaps_nonce',
 'swaps_logIndex',
 'swaps_gasLimit',
 'swaps_gasUsed',
 'swaps_gasPrice',
 'swaps_protocol_id',
 'swaps_account_id',
 'swaps_pool_id',
 'swaps_blockNumber',
 'swaps_tick',
 'swaps_tokenIn_id',
 'swaps_amountIn',
 'swaps_amountInUSD',
 'swaps_tokenOut_id',
 'swaps_amountOut',
 'swaps_amountOutUSD',
 'transaction_gas_fee_one_hop',
 'transaction_gas_fee_median']

In [114]:
# This truncated dataframe isn't being used right now
cow_uni_trunc_pl = cow_uni_outer_pl[[
    'trades_timestamp', 
    'trades_txHash',
    'trades_feeAmount',
    'trades_sellToken_id', 
    'trades_buyToken_id', 
    'trades_buyAmount',
    'trades_sellAmount',
    # 'trades_sellAmountUsd', 
    # 'trades_buyAmountUsd', 
    'name',
    'environment',
    'swaps_pool_id', 
    'swaps_hash',
    'swaps_tokenIn_id', 
    'swaps_tokenOut_id',
    'swaps_amountIn',
    'swaps_amountOut',  
    # 'swaps_amountInUSD',
    # 'swaps_amountOutUSD',
    'swaps_blockNumber',
    # 'transactions_timestamp',
    # 'transactions_gasUsed',
    # 'transactions_gasPrice',
    'transaction_gas_fee_one_hop',
    'transaction_gas_fee_median'
    ]]

In [115]:
#check pl dataframe size
cow_uni_trunc_pl.shape

(406372, 18)

In [116]:
# sort by largest transaction_gas_fee
cow_uni_trunc_pl.sort("transaction_gas_fee_one_hop", reverse=True).head(5)

shape: (5, 18)
┌────────────┬────────────┬────────────┬────────────┬─────┬────────────┬────────────┬────────────┬────────────┐
│ trades_tim ┆ trades_txH ┆ trades_fee ┆ trades_sel ┆ ... ┆ swaps_amou ┆ swaps_bloc ┆ transactio ┆ transactio │
│ estamp     ┆ ash        ┆ Amount     ┆ lToken_id  ┆     ┆ ntOut      ┆ kNumber    ┆ n_gas_fee_ ┆ n_gas_fee_ │
│ ---        ┆ ---        ┆ ---        ┆ ---        ┆     ┆ ---        ┆ ---        ┆ one_hop    ┆ median     │
│ i64        ┆ str        ┆ i64        ┆ str        ┆     ┆ str        ┆ i64        ┆ ---        ┆ ---        │
│            ┆            ┆            ┆            ┆     ┆            ┆            ┆ f64        ┆ f64        │
╞════════════╪════════════╪════════════╪════════════╪═════╪════════════╪════════════╪════════════╪════════════╡
│ 1655526233 ┆ null       ┆ null       ┆ null       ┆ ... ┆ 4109686609 ┆ 14983045   ┆ 5.432645   ┆ 13.355686  │
│            ┆            ┆            ┆            ┆     ┆ 43         ┆            ┆            ┆            │
│ 1672802939 ┆ null       ┆ null       ┆ null       ┆ ... ┆ 3386449138 ┆ 16330739   ┆ 5.294724   ┆ 13.016621  │
│            ┆            ┆            ┆            ┆     ┆ 4233445214 ┆            ┆            ┆            │
│            ┆            ┆            ┆            ┆     ┆ 9          ┆            ┆            ┆            │
│ 1655539351 ┆ null       ┆ null       ┆ null       ┆ ... ┆ 6691734542 ┆ 14983888   ┆ 4.773773   ┆ 11.735907  │
│            ┆            ┆            ┆            ┆     ┆ 4840932755 ┆            ┆            ┆            │
│            ┆            ┆            ┆            ┆     ┆ 1          ┆            ┆            ┆            │
│ 1655005971 ┆ null       ┆ null       ┆ null       ┆ ... ┆ 7284568702 ┆ 14948045   ┆ 3.893746   ┆ 9.572438   │
│            ┆            ┆            ┆            ┆     ┆ 2398390594 ┆            ┆            ┆            │
│            ┆            ┆            ┆            ┆     ┆ 3          ┆            ┆            ┆            │
│ 1635361917 ┆ null       ┆ null       ┆ null       ┆ ... ┆ 4372188863 ┆ 13501168   ┆ 3.729749   ┆ 9.169265   │
│            ┆            ┆            ┆            ┆     ┆ 4697712806 ┆            ┆            ┆            │
│            ┆            ┆            ┆            ┆     ┆ 8          ┆            ┆            ┆            │
└────────────┴────────────┴────────────┴────────────┴─────┴────────────┴────────────┴────────────┴────────────┘

In [117]:
sample_data = cow_uni_trunc_pl[['swaps_hash', 'transaction_gas_fee_one_hop']].sort("transaction_gas_fee_one_hop", reverse=True).head(5)

In [118]:
sample_data

shape: (5, 2)
┌─────────────────────────────────────┬─────────────────────────────┐
│ swaps_hash                          ┆ transaction_gas_fee_one_hop │
│ ---                                 ┆ ---                         │
│ str                                 ┆ f64                         │
╞═════════════════════════════════════╪═════════════════════════════╡
│ 0xa2852db8dc60f0e1760a2e15928589... ┆ 5.432645                    │
│ 0x375d4386a42faf838702e6ba76c588... ┆ 5.294724                    │
│ 0xa4f6af184b349679fa522eecd9f502... ┆ 4.773773                    │
│ 0x560dac63c27234d82e5f872b6f7fce... ┆ 3.893746                    │
│ 0x9654ebaa4f6d0df3371073b4678781... ┆ 3.729749                    │
└─────────────────────────────────────┴─────────────────────────────┘

In [119]:
sample_data['swaps_hash'].to_list()

['0xa2852db8dc60f0e1760a2e1592858997d22adb638befbe27ddcfe32986b06bbf',
 '0x375d4386a42faf838702e6ba76c588919ad3f8959b136679235fd16faf6fe71c',
 '0xa4f6af184b349679fa522eecd9f502279713f9749d841f472ebbe43a0cef2863',
 '0x560dac63c27234d82e5f872b6f7fce8d476eb00b9d9b95ff6287c4ec3d10cd4f',
 '0x9654ebaa4f6d0df3371073b467878192dc18394d35bf0a0f67b4e4c40ffd870a']

### Chainlink

In [120]:
# load streamer class
chain_ds = Streamer('https://api.thegraph.com/subgraphs/name/openpredict/chainlink-prices-subgraph')

In [121]:
chain_price_feed = "ETH/USD"

In [122]:
chain_dfs_list = []

In [123]:
# get a query field path from the query dictionary which is automatically populated in the Streamer object
chain_fp = chain_ds.queryDict.get('prices')

# add parameters to the settlements_qp.
chain_qp = chain_fp(
    first=query_size * 5,
    orderBy='timestamp',
    orderDirection='desc',
    where = {'timestamp_lt': timestamp, 'assetPair': chain_price_feed}
    )

# run query
chain_df = chain_ds.runQuery(chain_qp)

FIELD - prices


In [124]:
# drop prices_id, endpoint. 
chain_df = chain_df.drop(['prices_id', 'endpoint'], axis=1)
# divide prices_price by 1e8 to get the price in USD
chain_df['prices_price'] = chain_df['prices_price'] / 10 ** 8

In [125]:
chain_df.shape

(124876, 3)

In [126]:
chain_pl = pl.from_pandas(chain_df)

In [127]:
# outer merge chain_df with cow_uni_outer_pl on timestamp
cow_uni_chain_outer_pl = cow_uni_trunc_pl.join(other=chain_pl, left_on='trades_timestamp', right_on='prices_timestamp', how='outer')

In [128]:
cow_uni_chain_outer_pl.shape

(527322, 20)

### Price Calculations

#### Decimal Calculations

In [129]:
# add decimals to cow trades sell tokens
cow_uni_chain_outer_pl = cow_uni_chain_outer_pl.with_columns(
    [
        pl.col('trades_sellToken_id'),
        (
            pl.when(pl.col('trades_sellToken_id') == 'WETH')
            .then(18)
            .otherwise(6)
            .cast(pl.UInt8)
        ).alias('trades_sellToken_decimals'),
    ]
)

# add decimals to cow trades buy tokens
cow_uni_chain_outer_pl = cow_uni_chain_outer_pl.with_columns(
    [
        pl.col('trades_buyToken_id'),
        (
            pl.when(pl.col('trades_buyToken_id') == 'WETH')
            .then(18)
            .otherwise(6)
            .cast(pl.UInt8)
        ).alias('trades_buyToken_decimals'),
    ]
)

# add decimals to cow trades sell tokens
cow_uni_chain_outer_pl = cow_uni_chain_outer_pl.with_columns(
    [
        pl.col('swaps_tokenIn_id'),
        (
            pl.when(pl.col('swaps_tokenIn_id') == 'WETH')
            .then(18)
            .otherwise(6)
            .cast(pl.UInt8)
        ).alias('swaps_tokenIn_decimals'),
    ]
)

# add decimals to cow trades buy tokens
cow_uni_chain_outer_pl = cow_uni_chain_outer_pl.with_columns(
    [
        pl.col('swaps_tokenOut_id'),
        (
            pl.when(pl.col('swaps_tokenOut_id') == 'WETH')
            .then(18)
            .otherwise(6)
            .cast(pl.UInt8)
        ).alias('swaps_tokenOut_decimals'),
    ]
)

In [130]:
cow_uni_chain_outer_pl.columns # NOTE - the DF has transaction cols

['trades_timestamp',
 'trades_txHash',
 'trades_feeAmount',
 'trades_sellToken_id',
 'trades_buyToken_id',
 'trades_buyAmount',
 'trades_sellAmount',
 'name',
 'environment',
 'swaps_pool_id',
 'swaps_hash',
 'swaps_tokenIn_id',
 'swaps_tokenOut_id',
 'swaps_amountIn',
 'swaps_amountOut',
 'swaps_blockNumber',
 'transaction_gas_fee_one_hop',
 'transaction_gas_fee_median',
 'prices_assetPair_id',
 'prices_price',
 'trades_sellToken_decimals',
 'trades_buyToken_decimals',
 'swaps_tokenIn_decimals',
 'swaps_tokenOut_decimals']

#### Execution Price Calculations

In [131]:
# cast all of the columns as numerics
cow_uni_chain_outer_pl = cow_uni_chain_outer_pl.with_columns([
        pl.col('trades_sellAmount').cast(pl.Float64),
        pl.col('trades_buyAmount').cast(pl.Float64),
        pl.col('swaps_amountIn').cast(pl.Float64),
        pl.col('swaps_amountOut').cast(pl.Float64)
        ])

In [132]:
# NOTE - Polars can perform these calculations in-column. This means it can convert the values in place without creating a new column. The new column created here is more verbose, but is a good sanity check to see before/after results.
trades_swaps_converted_pl = cow_uni_chain_outer_pl.with_columns([
    (pl.col("trades_buyAmount") / (10**pl.col("trades_buyToken_decimals"))).alias('trades_buyAmount_converted'),
    (pl.col("trades_sellAmount") / (10**pl.col("trades_sellToken_decimals"))).alias('trades_sellAmount_converted'),
    (pl.col("swaps_amountIn") / (10**pl.col("swaps_tokenIn_decimals"))).alias('swaps_amountIn_converted'),
    (pl.col("swaps_amountOut") / (10**pl.col("swaps_tokenOut_decimals"))).alias('swaps_amountOut_converted'),
])

In [133]:
trades_swaps_converted_trunc_pl = trades_swaps_converted_pl.with_columns([
    (pl.col("trades_buyAmount_converted") / pl.col("trades_sellAmount_converted")).alias('trades_buy_sell_ratio'),
    (pl.col("trades_sellAmount_converted") / pl.col("trades_buyAmount_converted")).alias('trades_sell_buy_ratio'),
    (pl.col("swaps_amountIn_converted") / pl.col("swaps_amountOut_converted")).alias('swaps_amountIn_amountOut_ratio'),
    (pl.col("swaps_amountOut_converted") / pl.col("swaps_amountIn_converted")).alias('swaps_amountOut_amountIn_ratio'),
])

In [134]:
trades_swaps_converted_trunc_pl = trades_swaps_converted_trunc_pl[
    'trades_timestamp',
    'swaps_blockNumber',
    'trades_txHash',
    'trades_feeAmount',
    'trades_sellToken_id',
    'trades_buyToken_id',
    'trades_sellAmount_converted',
    'trades_buyAmount_converted',
    'name',
    'environment',
    'swaps_pool_id',
    'swaps_tokenIn_id',
    'swaps_tokenOut_id',
    'swaps_amountIn_converted',
    'swaps_amountOut_converted',
    'transaction_gas_fee_one_hop',
    'transaction_gas_fee_median',
    'trades_buy_sell_ratio',
    'trades_sell_buy_ratio',
    'swaps_amountIn_amountOut_ratio',
    'swaps_amountOut_amountIn_ratio',
    'prices_assetPair_id',
    'prices_price'
]

In [135]:
trades_swaps_converted_trunc_pl.shape

(527322, 23)

In [136]:
trades_swaps_converted_trunc_pl.head(10)

shape: (10, 23)
┌────────────┬────────────┬────────────┬────────────┬─────┬────────────┬────────────┬────────────┬────────────┐
│ trades_tim ┆ swaps_bloc ┆ trades_txH ┆ trades_fee ┆ ... ┆ swaps_amou ┆ swaps_amou ┆ prices_ass ┆ prices_pri │
│ estamp     ┆ kNumber    ┆ ash        ┆ Amount     ┆     ┆ ntIn_amoun ┆ ntOut_amou ┆ etPair_id  ┆ ce         │
│ ---        ┆ ---        ┆ ---        ┆ ---        ┆     ┆ tOut_ratio ┆ ntIn_ratio ┆ ---        ┆ ---        │
│ i64        ┆ i64        ┆ str        ┆ i64        ┆     ┆ ---        ┆ ---        ┆ str        ┆ f64        │
│            ┆            ┆            ┆            ┆     ┆ f64        ┆ f64        ┆            ┆            │
╞════════════╪════════════╪════════════╪════════════╪═════╪════════════╪════════════╪════════════╪════════════╡
│ 1648623560 ┆ 14486093   ┆ null       ┆ null       ┆ ... ┆ 0.000294   ┆ 3402.61272 ┆ null       ┆ null       │
│            ┆            ┆            ┆            ┆     ┆            ┆ 6          ┆            ┆            │
│ 1648623560 ┆ 14486093   ┆ null       ┆ null       ┆ ... ┆ 0.000294   ┆ 3402.55391 ┆ null       ┆ null       │
│            ┆            ┆            ┆            ┆     ┆            ┆ 9          ┆            ┆            │
│ 1648623522 ┆ 14486088   ┆ null       ┆ null       ┆ ... ┆ 0.000294   ┆ 3402.70699 ┆ null       ┆ null       │
│            ┆            ┆            ┆            ┆     ┆            ┆ 3          ┆            ┆            │
│ 1648623457 ┆ 14486086   ┆ null       ┆ null       ┆ ... ┆ 3406.13991 ┆ 0.000294   ┆ null       ┆ null       │
│            ┆            ┆            ┆            ┆     ┆ 3          ┆            ┆            ┆            │
│ ...        ┆ ...        ┆ ...        ┆ ...        ┆ ... ┆ ...        ┆ ...        ┆ ...        ┆ ...        │
│ 1648623378 ┆ 14486085   ┆ null       ┆ null       ┆ ... ┆ 3406.38980 ┆ 0.000294   ┆ ETH/USD    ┆ 3404.1115  │
│            ┆            ┆            ┆            ┆     ┆ 9          ┆            ┆            ┆            │
│ 1648623356 ┆ 14486084   ┆ 0x3a7e35d8 ┆ 2932098765 ┆ ... ┆ 0.000294   ┆ 3402.95704 ┆ null       ┆ null       │
│            ┆            ┆ 0a5b8cc4a3 ┆ 432098     ┆     ┆            ┆            ┆            ┆            │
│            ┆            ┆ 71036d19df ┆            ┆     ┆            ┆            ┆            ┆            │
│            ┆            ┆ 3e...      ┆            ┆     ┆            ┆            ┆            ┆            │
│ 1648623356 ┆ 14486084   ┆ 0x3a7e35d8 ┆ 2932098765 ┆ ... ┆ 0.000294   ┆ 3402.95704 ┆ null       ┆ null       │
│            ┆            ┆ 0a5b8cc4a3 ┆ 432098     ┆     ┆            ┆            ┆            ┆            │
│            ┆            ┆ 71036d19df ┆            ┆     ┆            ┆            ┆            ┆            │
│            ┆            ┆ 3e...      ┆            ┆     ┆            ┆            ┆            ┆            │
│ 1648623317 ┆ 14486082   ┆ null       ┆ null       ┆ ... ┆ 0.000294   ┆ 3402.97068 ┆ null       ┆ null       │
│            ┆            ┆            ┆            ┆     ┆            ┆ 5          ┆            ┆            │
└────────────┴────────────┴────────────┴────────────┴─────┴────────────┴────────────┴────────────┴────────────┘

### Save Data to a local parquet file

In [137]:
# checkpoint, save to parquet
trades_swaps_converted_trunc_pl.write_parquet('data/cow_uni_chain_outer_pl_historical.parquet')